<a href="https://colab.research.google.com/github/proppy/silicon-notebooks/blob/serv/serv-openlane-gf180mcu.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Digital inverter with OpenLane

```
Copyright 2022 Google LLC.
SPDX-License-Identifier: Apache-2.0
```

Run a simple digital inverter design thru the [OpenLane](https://github.com/The-OpenROAD-Project/OpenLane/) GDS to RTL flow targeting the [open source GF180MCU PDK](https://github.com/google/gf180mcu-pdk/).

In [1]:
#@title Install dependencies {display-mode: "form"}
#@markdown - Click the ▷ button to setup the digital design environment based on [conda-eda](https://github.com/hdl/conda-eda).

openlane_version = 'latest' #@param {type:"string"}
open_pdks_rev = '120b0bd69c745825a0b8b76f364043a1cd08bb6a' #@param {type:"string"}

if openlane_version == 'latest':
  openlane_version = ''

import os
import pathlib
import sys

!curl -Ls https://micro.mamba.pm/api/micromamba/linux-64/latest | tar -xj bin/micromamba
conda_prefix_path = pathlib.Path('conda-env')
CONDA_PREFIX = str(conda_prefix_path.resolve())
!bin/micromamba create --yes --prefix $CONDA_PREFIX
!echo 'python ==3.7*' >> {CONDA_PREFIX}/conda-meta/pinned
!CI=0 bin/micromamba install --quiet --yes --prefix $CONDA_PREFIX \
                     --channel litex-hub \
                     --channel main \
                     openlane={openlane_version}
!python -m pip install --no-binary gdstk gdstk tqdm
# install pdk manually: https://github.com/hdl/conda-eda/pull/238
pdk_root_path = conda_prefix_path / 'share/pdk'
pdk_root_path.mkdir(parents=True, exist_ok=True)
PDK_ROOT=str(pdk_root_path.resolve())
%env PDK_ROOT={PDK_ROOT}
!curl -L -O https://github.com/efabless/volare/releases/download/gf180mcu-{open_pdks_rev}/default.tar.xz
!xz --decompress --stdout default.tar.xz | tqdm --bytes --total=`xz --robot --list default.tar.xz | sed -n 2p | cut -f5` > default.tar
!tar -xvf default.tar -C {PDK_ROOT} gf180mcuC/ | tqdm --total=`tar -tf default.tar gf180mcuC/ | wc -l ` --null
PATH = os.environ['PATH']
LD_LIBRARY_PATH = os.environ.get('LD_LIBRARY_PATH', '')
%env CONDA_PREFIX={CONDA_PREFIX}
%env PATH={CONDA_PREFIX}/bin:{PATH}
%env LD_LIBRARY_PATH={CONDA_PREFIX}/lib:{LD_LIBRARY_PATH}
site_package_path = conda_prefix_path / 'lib/python3.7/site-packages'
sys.path.append(str(site_package_path.resolve()))



                                           __
          __  ______ ___  ____ _____ ___  / /_  ____ _
         / / / / __ `__ \/ __ `/ __ `__ \/ __ \/ __ `/
        / /_/ / / / / / / /_/ / / / / / / /_/ / /_/ /
       / .___/_/ /_/ /_/\__,_/_/ /_/ /_/_.___/\__,_/
      /_/

Empty environment created at prefix: /content/conda-env
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 509.0/509.0 KB 10.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for gdstk: filename=gdstk-0.9.35-cp38-cp38-linux_x86_64.whl size=781975 sha256=2011423369ccfc488ae378d3b76136925574d365f96f7013d234cc8436995240
  Stored in directory: /root/.cache/pip/wheels/46/d9/67/da53a82ae15905306855cc71e098c74021a06e73e8f3da414c
Successfully built gdstk
env: PDK_ROOT=/content/conda-env/share/pdk
  % Total    % Rece

## Write verilog

In [7]:
!git clone -b serial_dbg_if https://github.com/olofk/subservient
!git clone https://github.com/olofk/serv

Cloning into 'subservient'...
remote: Enumerating objects: 165, done.
remote: Counting objects: 100% (112/112), done.
remote: Compressing objects: 100% (73/73), done.
remote: Total 165 (delta 46), reused 77 (delta 33), pack-reused 53
Receiving objects: 100% (165/165), 196.64 KiB | 3.28 MiB/s, done.
Resolving deltas: 100% (53/53), done.
Cloning into 'serv'...
remote: Enumerating objects: 2570, done.
remote: Counting objects: 100% (705/705), done.
remote: Compressing objects: 100% (264/264), done.
remote: Total 2570 (delta 510), reused 515 (delta 435), pack-reused 1865
Receiving objects: 100% (2570/2570), 12.54 MiB | 28.46 MiB/s, done.
Resolving deltas: 100% (1620/1620), done.


## Write configuration

[Documentation](https://openlane.readthedocs.io/en/latest/reference/configuration.html)

In [30]:
%%writefile config.json
{
    "DESIGN_NAME": "subservient",
    "VERILOG_FILES": [
      "dir::serv/rtl/*.v",
      "dir::serv/serving/*.v",
      "dir::subservient/rtl/*.v"
    ],
    "CLOCK_TREE_SYNTH": true,
    "CLOCK_PORT": "i_clk",
    "CLOCK_PERIOD": 50,
    "FP_SIZING": "absolute",
    "DIE_AREA": "0 0 400 400",
    "PL_TARGET_DENSITY": 0.75,
    "DESIGN_IS_CORE": 0
}



Overwriting config.json


## Run OpenLane Flow
[OpenLane](https://openlane.readthedocs.io/en/latest/) is an automated [RTL](https://en.wikipedia.org/wiki/Register-transfer_level) to [GDSII](https://en.wikipedia.org/wiki/GDSII) flow based on several components including [OpenROAD](https://theopenroadproject.org/), [Yosys](https://yosyshq.net/yosys/), [Magic](http://www.opencircuitdesign.com/magic/), [Netgen](http://opencircuitdesign.com/netgen/) and custom methodology scripts for design exploration and optimization targeting [open source PDKs](https://github.com/google/open-source-pdks).

![img](https://openlane.readthedocs.io/en/latest/_images/flow_v1.png)

In [31]:
%env PDK=gf180mcuC
!flow.tcl -design .

env: PDK=gf180mcuC
OpenLane 2023.01.09_1_gac83c37-conda
All rights reserved. (c) 2020-2022 Efabless Corporation and contributors.
Available under the Apache License, version 2.0. See the LICENSE file for more details.

[WARNING]: OpenLane may not function properly: not enough values to unpack (expected 3, got 1)
The version of open_pdks used in building the PDK does not match the version OpenLane was tested on (installed: 120b0bd69c745825a0b8b76f364043a1cd08bb6a, tested: 327e268bdb7191fe07a28bd40eeac055bba9dffd)
This may introduce some issues. You may want to re-install the PDK by invoking `make pdk`.
[INFO]: Using configuration in 'config.json'...
[INFO]: PDK Root: /content/conda-env/share/pdk
[INFO]: Process Design Kit: gf180mcuC
[INFO]: Standard Cell Library: gf180mcu_fd_sc_mcu7t5v0
[INFO]: Optimization Standard Cell Library: gf180mcu_fd_sc_mcu7t5v0
[INFO]: Run Directory: /content/runs/RUN_2023.01.12_18.53.08
[INFO]: Preparing LEF files for the nom corner...
[STEP 1]
[INFO]: Running

## Display layout

In [32]:
import pathlib
import gdstk
import IPython.display

gdss = sorted(pathlib.Path('runs').glob('*/results/final/gds/*.gds'))
library = gdstk.read_gds(gdss[-1])
top_cells = library.top_level()
top_cells[0].write_svg('inverter.svg')
IPython.display.SVG('inverter.svg')

## Metrics

[Documentation](https://openlane.readthedocs.io/en/latest/reference/datapoint_definitions.html)


In [33]:
import pandas as pd
import pathlib

pd.options.display.max_rows = None
final_summary_reports = sorted(pathlib.Path('runs').glob('*/reports/metrics.csv'))
df = pd.read_csv(final_summary_reports[-1])
df.transpose()

0
design                                     /content
design_name                             subservient
config                      RUN_2023.01.12_18.53.08
flow_status                          flow completed
total_runtime                            0h2m54s0ms
routed_runtime                           0h2m24s0ms
(Cell/mm^2)/Core_Util                       4381.25
DIEAREA_mm^2                                   0.64
CellPer_mm^2                               2190.625
OpenDP_Util                                   28.07
Peak_Memory_Usage_MB                         530.46
cell_count                                     1402
tritonRoute_violations                            0
Short_violations                                  0
MetSpc_violations                                 0
OffGrid_violations                                0
MinHole_violations                                0
Other_violations                                  0
Magic_violations                                  0
antenna_violations                                0
lvs_total_errors                                 -1
cvc_total_errors                                 -1
klayout_violations                               -1
wire_length                                  134386
vias                                          16059
wns                                             0.0
pl_wns                                          0.0
optimized_wns                                   0.0
fastroute_wns                                   0.0
spef_wns                                        0.0
tns                                             0.0
pl_tns                                          0.0
optimized_tns                                   0.0
fastroute_tns                                   0.0
spef_tns                                        0.0
HPWL                                     82584514.0
routing_layer1_pct                              0.0
routing_layer2_pct                            30.05
routing_layer3_pct                            34.32
routing_layer4_pct                             6.23
routing_layer5_pct                            13.38
routing_layer6_pct                               -1
wires_count                                     941
wire_bits                                      3204
public_wires_count                              394
public_wire_bits                               2647
memories_count                                    0
memory_bits                                       0
processes_count                                   0
cells_pre_abc                                   909
AND                                              28
DFF                                              37
NAND                                             20
NOR                                              22
OR                                               71
XOR                                              29
XNOR                                              5
MUX                                             204
inputs                                          321
outputs                                         328
level                                            11
EndCaps                                         188
TapCells                                        912
Diodes                                            0
Total_Physical_Cells                           1100
CoreArea_um^2                            142380.672
power_slowest_internal_uW                        -1
power_slowest_switching_uW                       -1
power_slowest_leakage_uW                         -1
power_typical_internal_uW                        -1
power_typical_switching_uW                       -1
power_typical_leakage_uW                         -1
power_fastest_internal_uW                        -1
power_fastest_switching_uW                       -1
power_fastest_leakage_uW                         -1
critical_path_ns                                 -1
suggested_clock_period                        